# Linear Models (Hypothesis-Driven)

In [10]:
import glob
import os

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt

## Get Labels

In [11]:
wisc_label_path = "/imaging3/owenlab/bpho/Biobank Labels/Subjects_with_WISC.csv"
wisc_labels = pd.read_csv(wisc_label_path, index_col='assessment WISC,EID')
ids_with_labels = wisc_labels.index
# display(wisc_labels)

## Get Data

In [12]:
def get_id_from_path(path):
    normalized_path = os.path.normpath(path)
    path_components = normalized_path.split(os.sep)
    return path_components[-2][4:]

def has_label(subject_id):
    return True if subject_id in ids_with_labels else False

In [15]:
# Search for all functional connectivity files and read them into a
# numpy array.
fc_path = '/imaging3/owenlab/bpho/python_yeo_fc'
fc_paths = glob.glob(fc_path + '/**/yeo_fc.npy', recursive=True)

wisc_scaled_measure = [
    'WISC_BD_Scaled', 
    'WISC_Similarities_Scaled', 
    'WISC_MR_Scaled',
    'WISC_DS_Scaled',
    'WISC_Coding_Scaled',
    'WISC_Vocab_Scaled',
    'WISC_FW_Scaled',
    'WISC_VP_Scaled',
    'WISC_PS_Scaled',
    'WISC_SS_Scaled',
]
age_col = 'assessment Basic_Demos,Age'

fpn_indices = np.triu_indices(11, k=1)
dmn_indices = (np.triu_indices(8, k=1)[0] + 11, np.triu_indices(8, k=1)[1] + 11)

within_fpn = []
within_dmn = []
between_fpn_dmn = []
measures = {measure: [] for measure in wisc_scaled_measure}
ages = []

for path in fc_paths:
    subject_id = get_id_from_path(path)
    
    if not has_label(subject_id):
        continue
    
    subject_fc = np.load(path)
    within_fpn.append(subject_fc[fpn_indices])
    within_dmn.append(subject_fc[dmn_indices])
    between_fpn_dmn.append(subject_fc[:11, 11:].flatten('C'))

    ages.append(wisc_labels.at[subject_id, age_col])
    
    for measure in wisc_scaled_measure:
        measures[measure].append(
            wisc_labels.at[subject_id, f'assessment WISC,{measure}'])

print("Number of functional connectivities:", len(within_fpn))
print("Number of within-FPN connections:", within_fpn[0].shape)
print("Number of within-DMN connections:", within_dmn[0].shape)
print("Number of between-FPN-DMN connections:", between_fpn_dmn[0].shape)

Number of functional connectivities: 584
Number of within-FPN connections: (55,)
Number of within-DMN connections: (28,)
Number of between-FPN-DMN connections: (88,)


In [14]:
# Preprocess the connections by reducing them to the mean
def mean_connections(connections):
    means = [np.mean(sub) for sub in connections]
    return np.array(means)

In [18]:
X_fpn = mean_connections(within_fpn)
X_dmn = mean_connections(within_dmn)
X_fpn_dmn = mean_connections(between_fpn_dmn)
X = np.array([X_fpn, X_dmn, X_fpn_dmn])
X_names = ["FPN", "DMN", "FPN+DMN"]

selected_measure = 'WISC_Coding_Scaled'
y = np.array(measures[selected_measure])

print("X_fpn:", X_fpn.shape, "X_dmn:", X_dmn.shape,
      "X_fpn_dmn:", X_fpn_dmn.shape, "X:", X.shape, 
      "y shape:", y.shape)

X_fpn: (584,) X_dmn: (584,) X_fpn_dmn: (584,) X: (3, 584) y shape: (584,)


In [ ]:
data = X
for measure in wisc_scaled_measure:
    measure_data = np.array([measures[selected_measure]])
    data = np.append(data, measure_data, axis=0)

headers = np.array(X_names + wisc_scaled_measure)
data = data.T
print(data.shape, headers.shape)

df = pd.DataFrame(data, columns=headers)
display(df)
df.to_csv('/imaging3/owenlab/bpho/Biobank Labels/Yeo_WISC.csv', index=False)

## Linear Regression

In [7]:
from scipy import stats

In [37]:
y_preds = []
print(measure_text)

for network, name in zip(X, X_names):
    m, b, r, p, std_err = stats.linregress(network, y)
    print(f"{name}: y = {m:.2f}x + {b:.2f}, r = {r:.2f}, p = {p:.4f}")
    
    y_pred = m * network + b
    y_preds.append(y_pred)

FPN: y = 0.74x + 9.55, r = 0.03, p = 0.5253
DMN: y = 1.08x + 9.56, r = 0.04, p = 0.3735
FPN+DMN: y = 1.99x + 9.49, r = 0.07, p = 0.0832


In [38]:
network = 2  # FPN = 0, DMN = 1, FPN_DMN = 2
plt.figure(1, figsize=(10, 10), dpi=1200)
scatter = plt.scatter(X[network], y, c=ages, alpha=0.3, label='Ground Truth')
plt.plot(X[network], y_preds[network], alpha=0.5, color='red', label="Predictions")
plt.title(f'{X_names[network]} vs {measure_text}')
plt.xlabel(f'{X_names[network]} Mean Connectivity')
plt.ylabel(f'{measure_text}')
plt.legend(*scatter.legend_elements())
plt.show()

## PLS

In [7]:
from sklearn.cross_decomposition import PLSRegression
from sklearn.model_selection import train_test_split
from sklearn.metrics import r2_score

In [9]:
train_scores = []
test_scores = []
print("------------")
print(measure_text)

for network, name in zip(X, X_names):
    X_network = network.reshape(-1, 1)
    print(X_network.shape)
    train_scores = []
    test_scores = []
    
    for i in range(0, 1000):
        X_train, X_test, y_train, y_test = train_test_split(
            X_network, y, test_size=0.3)

        pls = PLSRegression(n_components=3)
        pls.fit(X_train, y_train)

        y_train_pred = pls.predict(X_train)
        y_test_pred = pls.predict(X_test)

        train_scores.append(r2_score(y_train, y_train_pred))
        test_scores.append(r2_score(y_test, y_test_pred))

    avg_train_score = np.mean(train_scores)
    avg_test_score = np.mean(test_scores)
    
    print("Network:", name)
    print("Train r^2:", avg_train_score)
    print("Test r^2:", avg_test_score)
    print("---")

------------
WISC_Vocab_Scaled
(584, 1)


/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24

/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24

/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24

/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24

...

/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24

/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24

/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24

Network: FPN+DMN
Train r^2: 0.0038691283240475044
Test r^2: -0.0090968188897271
---


/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24, n_components(3) should be in [1, n_features].n_components=1 will be used instead. In version 1.1 (renaming of 0.26), an error will be raised.
  FutureWarning
/home/bpho/.conda/envs/venv/lib/python3.7/site-packages/sklearn/cross_decomposition/_pls.py:191: FutureWarning: As of version 0.24

### Use all connections

In [ ]:
X = []
for subject in range(0, len(within_fpn)):
    X_subject = np.concatenate((within_fpn[subject], within_dmn[subject], between_fpn_dmn[subject]))
    X.append(X_subject)
X = np.array(X)
    
selected_measure = 'WISC_Vocab_Scaled'
y = np.array(measures[selected_measure])

print(X.shape, y.shape)

In [50]:
train_scores = []
test_scores = []

for i in range(0, 1000):
    X_train, X_test, y_train, y_test = train_test_split(
        X, y, test_size=0.3)
    
    pls = PLSRegression(n_components=2)
    pls.fit(X_train, y_train)

    y_train_pred = pls.predict(X_train)
    y_test_pred = pls.predict(X_test)
    
    train_scores.append(r2_score(y_train, y_train_pred))
    test_scores.append(r2_score(y_test, y_test_pred))

avg_train_score = np.mean(train_scores)
avg_test_score = np.mean(test_scores)

print("Train r^2:", avg_train_score)
print("Test r^2:", avg_test_score)
# plt.show()

Train r^2: 0.15310254725022424
Test r^2: -0.08422895364732914
